<a href="https://colab.research.google.com/github/Nick24-hub/Neural_Networks_Pac-Man/blob/main/Neural_Networks_Pac_Man.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

##Install packages

In [ ]:
!apt-get update > /dev/null 2>&1
!apt-get install cmake > /dev/null 2>&1
!pip install --upgrade setuptools 2>&1
!pip install ez_setup > /dev/null 2>&1
!pip install gym[atari] > /dev/null 2>&1

##Define display method

In [ ]:
!pip install gym pyvirtualdisplay > /dev/null 2>&1
!apt-get install -y xvfb python-opengl ffmpeg > /dev/null 2>&1

In [ ]:
import gym
from gym.wrappers import Monitor
import glob
import io
import base64
from IPython.display import HTML
from pyvirtualdisplay import Display
from IPython import display as ipythondisplay

display = Display(visible=0, size=(1400, 900))
display.start()

"""
Utility functions to enable video recording of gym environment 
and displaying it.
To enable video, just do "env = wrap_env(env)""
"""

def show_video():
  mp4list = glob.glob('video/*.mp4')
  if len(mp4list) > 0:
    mp4 = mp4list[0]
    video = io.open(mp4, 'r+b').read()
    encoded = base64.b64encode(video)
    ipythondisplay.display(HTML(data='''<video alt="test" autoplay 
                loop controls style="height: 400px;">
                <source src="data:video/mp4;base64,{0}" type="video/mp4" />
             </video>'''.format(encoded.decode('ascii'))))
  else: 
    print("Could not find video")
    

def wrap_env(env):
  env = Monitor(env, './video', force=True)
  return env

## Download ROM

In [ ]:
! wget http://www.atarimania.com/roms/Roms.rar
! mkdir /content/ROM/
! unrar e /content/Roms.rar /content/ROM/
! python -m atari_py.import_roms /content/ROM/

--2022-01-18 21:23:47--  http://www.atarimania.com/roms/Roms.rar
Resolving www.atarimania.com (www.atarimania.com)... 195.154.81.199
Connecting to www.atarimania.com (www.atarimania.com)|195.154.81.199|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 11128004 (11M) [application/x-rar-compressed]
Saving to: ‘Roms.rar’

Roms.rar            100%[===================>]  10.61M   833KB/s    in 14s     

2022-01-18 21:24:01 (795 KB/s) - ‘Roms.rar’ saved [11128004/11128004]


UNRAR 5.50 freeware      Copyright (c) 1993-2017 Alexander Roshal


Extracting from /content/Roms.rar

Extracting  /content/ROM/HC ROMS.zip                                      36%  OK 
Extracting  /content/ROM/ROMS.zip                                         74% 99%  OK 
All OK
copying adventure.bin from ROMS/Adventure (1980) (Atari, Warren Robinett) (CX2613, CX2613P) (PAL).bin to /usr/local/lib/python3.7/dist-packages/atari_py/atari_roms/adventure.bin
copying air_raid.bin fr

##Define the enviroment

In [ ]:
env = gym.make("MsPacman-ram-v0")

##Define the model

In [ ]:
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import models
from tensorflow.keras import layers
import numpy as np
import random
from google.colab import drive
drive.mount('/content/gdrive', force_remount=True)
from collections import deque

MessageError: ignored

In [ ]:
first_layer = layers.Dense(128, activation='relu', input_shape = (4 * len(env.reset()), ))
second_layer = layers.Dense(32, activation='relu')
third_layer = layers.Dense(9)


network = models.Sequential()

network.add(first_layer)
network.add(second_layer)
network.add(third_layer)

In [ ]:
network.compile(optimizer='adam',
                loss='mean_squared_error')

In [ ]:
network.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense (Dense)               (None, 128)               65664     
                                                                 
 dense_1 (Dense)             (None, 32)                4128      
                                                                 
 dense_2 (Dense)             (None, 9)                 297       
                                                                 
Total params: 70,089
Trainable params: 70,089
Non-trainable params: 0
_________________________________________________________________


In [ ]:
[print(i.shape, i.dtype) for i in network.inputs]
[print(o.shape, o.dtype) for o in network.outputs]

(None, 512) <dtype: 'float32'>
(None, 9) <dtype: 'float32'>


[None]

## Start learning process

In [ ]:
#network = tf.keras.models.load_model('gdrive/MyDrive/saved_model/V3_Reward1242_Episode218')

In [ ]:
exploration_prob = 1
min_exploration_prob = 0.01
exploration_decreasing_decay = 0.05
gamma = 0.01
max_gamma = 0.95
#gamma_increasing_decay = 1.3
replay_buffer = deque(maxlen=50000)

In [ ]:
dst='gdrive/MyDrive/saved_model/'
n_episodes = 100
n_iterations = 5

for episode in range(0,n_episodes):
  env = wrap_env(gym.make("MsPacman-ram-v0"))
  print("Episode",episode,":")
  for iteration in range(n_iterations):
    state = state1 = state2 = state3 = env.reset()
    last_reward = 0
    penalty = 0
    while True:
      last_4_states = np.concatenate(( state3, state2, state1, state), axis=None)
      last_4_states = np.reshape(last_4_states, (len(last_4_states), -1))
      prediction = network.predict(last_4_states.T)
      if np.random.uniform(0, 1) < exploration_prob:
        action = env.action_space.sample()
      else:
        action = np.argmax(prediction)
      next_state, reward, done, number_of_lives_left = env.step(action)
      if last_reward == 0 and reward == 0:
        penalty = penalty + 1
        reward = reward - penalty
      else:
        penalty = 0
      replay_buffer.append((state, action, next_state, reward, prediction.T))
      state3 = np.copy(state2)
      state2 = np.copy(state1)
      state1 = np.copy(state)
      state = next_state
      if done:
        break;
            
  
  #Prepare data and labels for training
  x= list()
  y= list()
  len_of_buffer=len(replay_buffer)
  list_of_indexes = random.sample([i for i in range(3,len_of_buffer-1)], len_of_buffer//10)
  for index in list_of_indexes:
    last_4_states = np.concatenate(( replay_buffer[index-3][0], replay_buffer[index-2][0], replay_buffer[index-1][0], replay_buffer[index][0]), axis=None)
    x.append(last_4_states)
    y.append(replay_buffer[index][4])
    next_prediction = replay_buffer[index+1][4]
    y[-1][replay_buffer[index][1]] = replay_buffer[index][3] + gamma * np.max(next_prediction)
  x=np.asarray(x).astype(np.float32)
  y=np.asarray(y).astype(np.float32)

  #Train network
  network.fit(x, y, epochs = 2, verbose=1)

  # Update  gamma and exploration_prob
  exploration_prob = max(min_exploration_prob, np.exp(-exploration_decreasing_decay * (episode + 1)))
  gamma = min(max_gamma,  1 - exploration_prob)

  # Print the result
  total_reward = 0
  for test in range(5):
    env = wrap_env(gym.make("MsPacman-ram-v0"))
    state = state1 = state2 = state3 = env.reset()
    while True:
      last_4_states = np.concatenate(( state3, state2, state1, state), axis=None)
      state3 = np.copy(state2)
      state2 = np.copy(state1)
      state1 = np.copy(state)
      last_4_states = np.reshape(last_4_states, (len(last_4_states), -1))
      prediction = network.predict(last_4_states.T)
      action = np.argmax(prediction)
      state, reward, done, number_of_lives_left = env.step(action)
      total_reward += reward
      if done:
        break;        
    env.close()
    show_video()

  print("Mean reward:",total_reward/5)

  #Save model
  network.save(dst+"V4_Reward"+str(int(total_reward/5))+"_Episode"+str(episode))
  

##Run the game

In [ ]:
network = tf.keras.models.load_model('gdrive/MyDrive/saved_model/V3_Reward1198_Episode142')

In [ ]:
total_reward = 0
for episode in range(10):
  env = wrap_env(gym.make("MsPacman-ram-v0"))
  state = state1 = state2 = state3 = env.reset()
  while True:
    last_4_states = np.concatenate(( state3, state2, state1, state), axis=None)
    state3 = np.copy(state2)
    state2 = np.copy(state1)
    state1 = np.copy(state)
    last_4_states = np.reshape(last_4_states, (len(last_4_states), -1))
    prediction = network.predict(last_4_states.T)
    action = np.argmax(prediction)
    state, reward, done, number_of_lives_left = env.step(action)
    total_reward += reward
    if done:
      break;        
  env.close()
  show_video()
print("Mean reward:",total_reward/10)

Mean reward: 820.0


In [ ]:
network = tf.keras.models.load_model('gdrive/MyDrive/saved_model/V3_Reward1242_Episode218')

In [ ]:
total_reward = 0
for episode in range(10):
  env = wrap_env(gym.make("MsPacman-ram-v0"))
  state = state1 = state2 = state3 = env.reset()
  while True:
    last_4_states = np.concatenate(( state3, state2, state1, state), axis=None)
    state3 = np.copy(state2)
    state2 = np.copy(state1)
    state1 = np.copy(state)
    last_4_states = np.reshape(last_4_states, (len(last_4_states), -1))
    prediction = network.predict(last_4_states.T)
    action = np.argmax(prediction)
    state, reward, done, number_of_lives_left = env.step(action)
    total_reward += reward
    if done:
      break;        
  env.close()
  show_video()
print("Mean reward:",total_reward/10)

Mean reward: 1144.0
